In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from scripts.hydraulic import hydr

import io
import PIL

# <center/> Расчет нестационарного течения жидкости в нефтепроводе

In [2]:
# Исходные данные
L = 100 # Длина участка, км 
dx = 1 # Шаг расчета параметров, км
c = 1000 # Скорость распространения волн давления в трубопроводе(для нефти примерное значение, зависит от многих факторов), м/с
d = 1000 # Внутренний диаметр, мм
D = 1020 # Наружный диаметр, мм
rho = 1000 # Плотность жидкости, кг/м^3
Ny = 1 # Кинематическая вязкость, сСт
w0 = 2.7 # Скорость жидкости в трубопроводе в стационарном режиме, м/с
a = 220 # Коэффициент аппроксимации характеристики насоса, м
b = 8.88e-07 # Коэффициент аппроксимации характеристики насоса, ч^2/м^5
hp = 50 # Подпор в начале участка, м
tao = 300 # Период времени для расчета параметров жидкости вы трубопроводе, с
pressureRiseTime = 100 # Время, в которое происходит повышение давления, начиная с начала отсчета, с
deltaP = 1.5 # Величина повышения давления, МПа
xsi = 0.21 # Коэффициент местного сопротивления клапана
Svalve = np.pi * 0.1**2 / 4 # Площадь клапана, м^2
valveCoord = 80 # Координата установки предохранительного клапана, км
PstartOpening = 2.5 # Давление начала открытия предохранительного клапана, МПа

In [3]:
# Инициализация расчетного класса
hydr = hydr(d=d,
            D=D,
            Ny=Ny,
            rho=rho,
            dx=dx,
            c=c,
            a=a,
            b=b,
            hp=hp,
            xsi=xsi,
            Svalve=Svalve,
            PstartOpening=PstartOpening
            )

In [4]:
# Временной интервал измерения, с
dt = dx * 1000 / c

Q = w0 * np.pi * d**2 / 4 / 10**6 * 3600 # Расход в м^3/ч
P0 = rho * 9.81 * (hp+3*(a-b*Q**2)) / 10**6 # Начальное давление, МПа

# Задаем таблицы скорости и давления
flowRate = pd.DataFrame(columns=range(0, int(L*1000) + 1, int(dx*1000)), index=[0], data=w0)

pressure = pd.DataFrame(columns=range(0, int(L*1000) + 1, int(dx*1000)), index=[0], data=P0)

# Расчет падения давления по длине трубопровода
for i, x in enumerate(pressure.columns[1:]):
    pressure.iloc[0, i+1] = pressure.iloc[0, 0] - hydr.i(w0)*x/10**6
    
pressure = pressure.round(3)

# Количество строк для добавления
strCount = int(np.ceil(tao / dt))

# Границы участков
leftBound = 0
rightBound = len(pressure.columns) - 1

In [5]:
# Slider
traceListPressure = [
    go.Scatter(visible=True, x=pressure.columns/1000, y=pressure.iloc[0, :], mode='lines', name=0)
]

traceListRate = [
    go.Scatter(visible=True, x=flowRate.columns/1000, y=flowRate.iloc[0, :], mode='lines', name=0)
]

## Animation

traceListPressureAnime = [
    go.Scatter(x=pressure.columns/1000, y=pressure.iloc[0, :], mode='lines', name=0)
]

traceListRateAnime = [
    go.Scatter(x=flowRate.columns/1000, y=flowRate.iloc[0, :], mode='lines', name=0)
]

##

KvalveLst = [] # Список степеней открытия клапана в каждый момент времени

# Расчет давления и скорости для указанного времени с заданным интервалом по длине трубопровода
for counter in range(1, strCount + 1):
    pressure.loc[counter * dt, :] = 0
    flowRate.loc[counter * dt, :] = 0
    
    for i, x in enumerate(pressure.columns):
        
        # Левая граница
        
        if i == leftBound:
            # Параметры рассматриваемой точки
            pressure.iloc[-1, i] = hydr.Pc(Pb=pressure.iloc[-2, i + 1], wb=flowRate.iloc[-2, i + 1], leftBound=True)
            flowRate.iloc[-1, i] = hydr.wc(Pb=pressure.iloc[-2, i + 1], wb=flowRate.iloc[-2, i + 1], leftBound=True)
            
        # Правая граница
        
        elif i == rightBound: 
            # Параметры рассматриваемой точки
            
            # Учитываем время изменения давления
            if pressure.index[-1] == pressureRiseTime:
                Pc = pressure.iloc[-1, i] = pressure.iloc[-2, rightBound] + deltaP
            else:
                Pc = pressure.iloc[-1, i] = pressure.iloc[-2, rightBound]
            
            flowRate.iloc[-1, i] = hydr.wc(Pa=pressure.iloc[-2, i - 1], wa=flowRate.iloc[-2, i - 1], rightBound=True, Pc=Pc)
        
        # Предохранительный клапан
        
        # Предыдущая точка
        
        elif (x == (valveCoord-dx) * 10**3) & (counter >= 2):
             
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = hydr.wc(pressure.iloc[-3, i],
                         pressure.iloc[-3, i + 2],
                         flowRate.iloc[-3, i],
                         flowRate.iloc[-3, i + 2],
                         valve=True
                         )[0]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]
                
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)

        # Следующая точка
        
        elif (x == (valveCoord+dx) * 10**3) & (counter >= 2):
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = hydr.wc(pressure.iloc[-3, i - 2],
                         pressure.iloc[-3, i],
                         flowRate.iloc[-3, i - 2],
                         flowRate.iloc[-3, i],
                         valve=True
                         )[1]
            
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
                
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)
                
        # Сам клапан
        
        elif x == valveCoord * 10**3:
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]

            # Параметры рассматриваемой точки
            Pc = pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb, valve=True)
            wprev, wnext, marker = hydr.wc(Pa, Pb, wa, wb, valve=True)
            
            flowRate.iloc[-1, i] = wprev 
            
            # Степень открытия клапана
            KvalveLst.append(marker)
            
        # Промежуточные точки
        
        else:
            # Параметры следующей точки
            Pb = pressure.iloc[-2, i + 1]
            wb = flowRate.iloc[-2, i + 1]
            
            # Параметры предыдущей точки
            Pa = pressure.iloc[-2, i - 1]
            wa = flowRate.iloc[-2, i - 1]

            # Параметры рассматриваемой точки
            pressure.iloc[-1, i] = hydr.Pc(Pa, Pb, wa, wb)
            flowRate.iloc[-1, i] = hydr.wc(Pa, Pb, wa, wb)
            
    if marker:
        flowRatey = flowRate.loc[counter * dt, :(valveCoord-dx)*1000].to_list() + [wprev, wnext] + flowRate.loc[counter * dt, (valveCoord+dx)*1000:].to_list()
        flowRatex = flowRate.loc[counter * dt, :(valveCoord-dx)*1000].index.to_list() + [valveCoord*1000, valveCoord*1000] + flowRate.loc[counter * dt, (valveCoord+dx)*1000:].index.to_list()
        
        traceListRate.append(go.Scatter(visible=False, x=np.array(flowRatex)/1000, y=flowRatey, mode='lines', name=counter * dt))
        traceListRateAnime.append(go.Scatter(x=np.array(flowRatex)/1000, y=flowRatey, mode='lines', name=counter * dt))
    else:
        traceListRate.append(go.Scatter(visible=False, x=flowRate.columns/1000, y=flowRate.loc[counter * dt, :], mode='lines', name=counter * dt))
        traceListRateAnime.append(go.Scatter(x=flowRate.columns/1000, y=flowRate.loc[counter * dt, :], mode='lines', name=counter * dt))
        
    traceListPressure.append(go.Scatter(visible=False, x=pressure.columns/1000, y=pressure.loc[counter * dt, :], mode='lines', name=counter * dt))
    traceListPressureAnime.append(go.Scatter(x=pressure.columns/1000, y=pressure.loc[counter * dt, :], mode='lines', name=counter * dt))






display(pressure)
display(flowRate)

0       1000    2000    3000    4000    5000    6000    7000    8000    \
0     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
1     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
2     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
3     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
4     5.442   5.393   5.344   5.295   5.246   5.196   5.147   5.098   5.049   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
296   5.757   5.715   5.676   5.639   5.418   5.377   5.516   5.472   5.352   
297   5.756   5.717   5.677   5.459   5.419   5.555   5.513   5.394   5.350   
298   5.757   5.718   5.503   5.460   5.593   5.552   5.434   5.392   5.340   
299   5.757   5.545   5.504   5.634   5.590   5.473   5.432   5.381   5.344   
300   5.584   5.546   5.673   5.631   5.515   5.472   5.420   5.384   5.433   

     9000    ...  91000   92000   93000   94000   95000   96000   97000   \
0     5.000  ...   0.972   0.923   0.874   0.825   0.776   0.727   0.678   
1     5.000  ...   0.973   0.923   0.874   0.825   0.776   0.727   0.678   
2     5.000  ...   0.972   0.924   0.874   0.825   0.776   0.727   0.678   
3     5.000  ...   0.973   0.923   0.874   0.825   0.776   0.727   0.678   
4     5.000  ...   0.972   0.924   0.874   0.825   0.776   0.727   0.677   
..      ...  ...     ...     ...     ...     ...     ...     ...     ...   
296   5.309  ...   2.164   1.623   1.608   2.071   1.569   1.558   2.616   
297   5.298  ...   1.637   1.624   2.080   1.582   1.571   2.040   2.085   
298   5.301  ...   1.636   2.089   1.598   1.585   2.049   2.092   2.084   
299   5.393  ...   2.097   1.610   1.599   2.060   2.101   2.093   1.522   
300   5.393  ...   1.623   1.612   2.068   2.110   2.104   1.537   1.523   

     98000   99000   100000  
0     0.629   0.580    0.53  
1     0.629   0.580    0.53  
2     0.629   0.579    0.53  
3     0.628   0.579    0.53  
4     0.628   0.579    0.53  
..      ...     ...     ...  
296   2.654   2.626    2.03  
297   2.655   2.066    2.03  
298   1.510   2.066    2.03  
299   1.509   1.482    2.03  
300   1.494   1.481    2.03  

[301 rows x 101 columns]

0       1000    2000    3000    4000    5000    6000    7000    8000    \
0     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
1     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
2     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
3     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
4     2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
296   2.405   2.404   2.403   2.404   2.585   2.588   2.403   2.405   2.485   
297   2.406   2.405   2.403   2.581   2.585   2.403   2.407   2.486   2.488   
298   2.405   2.405   2.580   2.581   2.402   2.407   2.485   2.489   2.498   
299   2.405   2.577   2.580   2.404   2.406   2.483   2.487   2.497   2.496   
300   2.571   2.577   2.404   2.408   2.484   2.485   2.494   2.494   2.403   

     9000    ...  91000   92000   93000   94000   95000   96000   97000   \
0     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
1     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
2     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
3     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.700   
4     2.700  ...   2.700   2.700   2.700   2.700   2.700   2.700   2.701   
..      ...  ...     ...     ...     ...     ...     ...     ...     ...   
296   2.488  ...   1.140   1.668   1.674   1.193   1.687   1.690   1.794   
297   2.498  ...   1.663   1.671   1.192   1.681   1.683   1.196   1.144   
298   2.495  ...   1.664   1.192   1.678   1.677   1.195   1.142   1.142   
299   2.402  ...   1.190   1.671   1.672   1.196   1.142   1.141   1.702   
300   2.405  ...   1.665   1.665   1.194   1.142   1.142   1.697   1.702   

     98000   99000   100000  
0     2.700   2.700   2.700  
1     2.700   2.700   2.701  
2     2.700   2.701   2.701  
3     2.701   2.701   2.701  
4     2.701   2.701   2.701  
..      ...     ...     ...  
296   1.734   1.725   2.301  
297   1.733   2.301   2.301  
298   1.710   2.301   2.301  
299   1.708   1.718   2.301  
300   1.710   1.716   1.150  

[301 rows x 101 columns]

In [6]:
# Графическое отображение

# Давление
num_steps = len(pressure.index)


fig = go.Figure(data=traceListPressure)

steps = []
for i in range(num_steps):
    step = dict(
        method = 'restyle',
        args = ['visible', [False] * len(fig.data)],
    )
    step['args'][1][i] = True
    steps.append(step)

sliders = [dict(
    currentvalue = {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 10}},
    len = 0.9,
    x = 0.1,
    pad = {"b": 10, "t": 50},
    steps = steps,
)]

fig.update_layout(
    title='Распределение давления',
    xaxis_title='X, км',
    yaxis_title='P, МПа',
    height=800,
    width=1000,
    yaxis_range=[0, 10]
)

fig.layout.sliders = sliders

#fig.write_html('pressureDestribution.html')
fig.show()

In [7]:
# Скорость
num_steps = len(flowRate.index)



fig = go.Figure(data=traceListRate)

steps = []
for i in range(num_steps):
    step = dict(
        method = 'restyle',
        args = ['visible', [False] * len(fig.data)],
    )
    step['args'][1][i] = True
    steps.append(step)

sliders = [dict(
    currentvalue = {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 10}},
    len = 0.9,
    x = 0.1,
    pad = {"b": 10, "t": 50},
    steps = steps,
)]

fig.update_layout(
    title='Распределение скорости',
    xaxis_title='X, км',
    yaxis_title='w, м/с',
    height=800,
    width=1000,
    yaxis_range=[0, 5]
)

fig.layout.sliders = sliders

#fig.write_html('flowRateDestribution.html')
fig.show()

In [8]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=pressure.index,
        y=np.array(KvalveLst) * 100
    )
)

fig.update_layout(
    height=1000,
    width=1500,
    xaxis_title='$$t, c$$',
    yaxis_title=r'$$\eta, %$$'
)

fig.update_xaxes(title_font_size=30)
fig.update_yaxes(title_font_size=30)

fig.show()

#fig.write_html('valveOpening.html')

In [9]:
fig = make_subplots(2)

fig.add_trace(
    traceListPressureAnime[0],
    row=1,
    col=1
)

fig.add_trace(
    traceListRateAnime[0],
    row=2,
    col=1
)

num_steps = len(flowRate.index) - 1
frames = []

for i in range(1, num_steps + 1):
    frames.append(
        go.Frame(data=[traceListPressureAnime[i], traceListRateAnime[i]], traces=[0, 1], name=str(i))
    )
    
fig.frames = frames

fig.update_layout(legend_orientation="h",
                  legend=dict(x=.5, xanchor="center"),
                  updatemenus=[dict(direction="left", x=0.5, xanchor="center", y=0,
                                    type="buttons", buttons=[dict(label="►", method="animate", args=[None, {"frame": {"duration": 120, 
                                                                                                                      "redraw": False},
                                                                                                            "fromcurrent": True, 
                                                                                                            "transition": {"duration": 5}}]),
                                                             dict(label="❚❚", method="animate", args=[[None], {"frame": {"duration": 0, "redraw": False},
                                                                                                               "mode": "immediate",
                                                                                                               "transition": {"duration": 0}}])])],
                  margin=dict(l=0, r=0, t=0, b=0))


fig.update_layout(
    height=800,
    width=1500,
    showlegend=False
)

fig.update_xaxes(title=r'$$x, км$$', col=1, row=1)
fig.update_yaxes(title=r'$$P, МПа$$', range=[0, 8], col=1, row=1)
fig.update_yaxes(title=r'$$\upsilon,\text{м/с}$$', range=[0, 5], col=1, row=2)

def frame_args(duration):
    return {
            "frame": {"duration": duration + 115, 'redraw': False},
            "fromcurrent": True,
            "transition": {"duration": duration},
        }

sliders = [
            {
                'currentvalue': {"prefix": "Секунд с начала отсчета: ", 'suffix': 'c', "font": {"size": 20}},
                "pad": {"b": 10, "t": 60},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "steps": [
                    {
                        "args": [[f.name], frame_args(5)],
                        "label": str(k),
                        "method": "animate",
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]

fig.update_xaxes(title_font_size=20)
fig.update_yaxes(title_font_size=20)

fig.layout.sliders = sliders

fig.show()

In [11]:
frames = []
for s, fr in enumerate(fig.frames):
    # set main traces to appropriate traces within plotly frame
    fig.update(data=fr.data)
    # move slider to correct place
    fig.layout.sliders[0].update(active=s)
    # generate image of current state
    frames.append(PIL.Image.open(io.BytesIO(fig.to_image(format="png"))))
    
# create animated GIF
frames[0].save(
        "test.gif",
        save_all=True,
        append_images=frames[1:],
        optimize=True,
        duration=125,
        loop=0,
    )